In [34]:
import sys
import aerosandbox as asb
import aerosandbox.numpy as np
import matplotlib.pyplot as plt
import aerosandbox.tools.pretty_plots as p

### First We Define Trainer Geometry
This is a straightforward process thanks to [aerosandbox](https://github.com/peterdsharpe/AeroSandbox)
- For any airplane -`Airplance` Object- we can define the following:
	- A `Wing` object: This include all types of wing surfaces, including main wing, Horizontal, and Vertical Tail.
		- For each wing we define:
			- its name; (eg. 'main wing', 'horizontal tail')
			- leading edge coordinates w.r.t airplane reference point
			- Wing_sections such that each section has:
				- Leading edge coordinates w.r.t the wing's reference point (stated above)
				- chord
				- twist
				- airfoil
	- A `Fuselage` object: its definition is very similar to the wing's definition
		- The FuselageXSectoins however are defined in terms of [superellipse paramaters](https://en.wikipedia.org/wiki/Superellipse)
			- for a square cross section: `shape = infinity (any number > 5)`
			- for circular cross section: shape = `shape = 2`
	- A reference point for Moment calculations `xyz_ref` (i.e. The C.G)
	- Reference Length `b_ref`: by default wing's span
	- Reference Area `s_ref`: by default wing's area

In [35]:
# Trainer Definition
wing_airfoil = asb.Airfoil('clarky')
tail_airfoil = asb.Airfoil('naca0012')

wing = asb.Wing(
    name = 'main wing',
    xyz_le = [0,0,0],
    symmetric=True,
    xsecs=[
        asb.WingXSec(  # Root
            xyz_le=[0, 0, 0],
            chord=0.24988,
            twist=0,  # degrees
            airfoil=wing_airfoil,
        ),
        asb.WingXSec(  # Mid
            xyz_le=[0, 1.4/2, 0],
            chord=0.24988,
            twist=0,  # degrees
            airfoil=wing_airfoil,
            )]
)

htail = asb.Wing(
            name="Horizontal Stabilizer",
            symmetric=True,
            xsecs=[
                asb.WingXSec(  # root
                    xyz_le=[0, 0, 0],
                    chord=0.175,
                    twist=-2.5,                          # Tilt Angle
                    airfoil=tail_airfoil,
                    control_surfaces= [asb.ControlSurface(
                        name="Elevator",
                        symmetric=True,
                        trailing_edge=True,
                        hinge_point=0.75,
                        deflection=10,
                    )],

                ),
                asb.WingXSec(  # tip
                    xyz_le=[(170.5-79.61)/1000, 0.2, 0],
                    chord=79.61/1000,
                    twist=-2.5,
                    airfoil=tail_airfoil
                )
            ]
        )

vtail = asb.Wing(
            name="Vertical Stabilizer",
            symmetric=False,
            xsecs=[
                asb.WingXSec(
                    xyz_le=[0, 0, 0],
                    chord=0.175,
                    twist=0,
                    airfoil=tail_airfoil,
                    control_surface_is_symmetric=True,  # Rudder
                    control_surface_deflection=0,
                ),
                asb.WingXSec(
                    xyz_le=[(170.5-89.72)/1000, 0, 0.24964],
                    chord=89.72/1000,
                    twist=0,
                    airfoil=tail_airfoil
                )
            ]
        )
fuselage=asb.Fuselage(
            name="Fuselage",
            xsecs=[
                asb.FuselageXSec(
                    xyz_c=[-0.17, 0,-0.04],
                    height=0.08,
                    width=0.11,
                    shape=100           # Square Cross Section
                ),
                asb.FuselageXSec(
                    xyz_c = [0.46 - 0.17, 0, -0.04],
                    height=0.08,
                    width=0.11,
                    shape=100            # Square Cross Section
                ),
                asb.FuselageXSec(
                    xyz_c=[0.9-0.17, 0, -(80-(899.85-460)*np.sind(4.3))/2/1000],
                    height=(80-(899.85-460)*np.sind(4.3))/1000,
                    width=0.045,
                    shape=100            # Square Cross Section
                )

            ]
        )
# Complete Airplane
trainer = asb.Airplane(
    name = 'trainer',
    xyz_ref=[0.073,0,-0.05],
    s_ref=wing.area(),
    b_ref=wing.span(),
    wings = [
        wing, # main wing
        htail.translate([612.34/1000,0,-0.025]), # Horizontal Tail (translated with L=Tail arm)
        vtail.translate([612.34/1000,0,-0.025])  # Vertical Tail (translated with L=Tail arm)
    ],
    fuselages=[fuselage]
)

### First we define the plane's weight

In [3]:
W = 1.3*9.81

### Then Define the Atmospheric Condition
Sets up the air properties at certain altitude

In [4]:
atm = asb.Atmosphere(altitude=30)   # Atmoshpere at 30 m above SL

### 3. Optimization Framework
- `Opti` constructs a nonlinear program (NLP) with decision variables, constraints, and objectives.
- Default solver: **IPOPT**.
- in a simple terms: Makes a virtual calculator that tries different combinations of speed/angle to find what works (according to a later-specified objective and constraints)

In [35]:
opti = asb.Opti()                   # Optimization instance

### 4. Decision Variables & OperatingPoint
- **`OperatingPoint`** bundles: air properties + kinematics.
- **`velocity` (V)** and **`alpha` (α)** are continuous variables; bounds ensure physically plausible flight.
	- We can specify certain velue or array of values however here we don't know the cruising condition so we'll leave it to the optimizer

In [36]:
all_op_point_vlm = asb.OperatingPoint(   # This is a vague operating point that doesn't specify any alpha or velocity, ...
                                         # ... They will be determined later when optimizing the solution
    atmosphere=atm,
    velocity=opti.variable(
        init_guess=14,
        lower_bound=13, 
        upper_bound=50,
    ),
    alpha=opti.variable(
        init_guess=0,
        lower_bound=-1,
        upper_bound=10,
    )
)

### Aerodynamic Analysis via VLM
Here we solve the problem using VLM (the method used in XFLR5). To perform the solution, we need to specify the `airplane` and `op_point`, which we previously defined to be `trainder` and `all_op_point_vlm` respectively



In [37]:
vlm_results = asb.VortexLatticeMethod(airplane=trainer, op_point=all_op_point_vlm, spanwise_resolution=30, chordwise_resolution=10).run()
vlm_L = vlm_results["L"]   # lift force [N] computed via VLM
vlm_D = vlm_results["D"]   # drag force [N] computed via VLM
vlm_Cm = vlm_results["Cm"] # Moment Coefficient computed via VLM

### Trim Constraints
Here we run the vlm problem under the optimization module, constraining the problem to the 2 trim conditions
- Lift = Weight
- $\Sigma M = 0$ (for faster solution we can set it to a very small number)

In [38]:
opti.subject_to(vlm_L == W)           # Lift = Weight Constraint
opti.subject_to(vlm_Cm <= 1e-8)      # Moment = 0
opti.subject_to(vlm_Cm >= -1e-8)
sol = opti.solve();                    # solve the optimization problem and assign it to `sol` variable

This is Ipopt version 3.14.11, running with linear solver MUMPS 5.4.1.

Number of nonzeros in equality constraint Jacobian...:        2
Number of nonzeros in inequality constraint Jacobian.:        8
Number of nonzeros in Lagrangian Hessian.............:        3

Total number of variables............................:        2
                     variables with only lower bounds:        0
                variables with lower and upper bounds:        0
                     variables with only upper bounds:        0
Total number of equality constraints.................:        1
Total number of inequality constraints...............:        6
        inequality constraints with only lower bounds:        3
   inequality constraints with lower and upper bounds:        0
        inequality constraints with only upper bounds:        3

iter    objective    inf_pr   inf_du lg(mu)  ||d||  lg(rg) alpha_du alpha_pr  ls
   0  0.0000000e+00 4.34e+00 0.00e+00   0.0 0.00e+00    -  0.00e+00 0.00e+00 

--------
### Extracting the results
Here we simply print the obtained cruise conditions

In [39]:
vlm_cruise_results = asb.VortexLatticeMethod(airplane=trainer, op_point=sol.value(all_op_point_vlm),spanwise_resolution=30, chordwise_resolution=10).run()
vlm_cruise_aoa = sol.value(all_op_point_vlm).alpha
vlm_cruise_v = sol.value(all_op_point_vlm).velocity
vlm_cruise_cl = vlm_cruise_results['CL']
vlm_cruise_cd = vlm_cruise_results['CD']
print("------------------------- cruise conditions from VLM -------------------------")
print(f"Angle of attack: {vlm_cruise_aoa:.4f} degree")
print(f"Velocity: {vlm_cruise_v:.4f} m/s")
print(f"CL: {vlm_cruise_cl:.4f}")
print(f"CD: {vlm_cruise_cd:.4f}")

------------------------- cruise conditions from VLM -------------------------
Angle of attack: 0.7733 degree
Velocity: 15.1051 m/s
CL: 0.2616
CD: 0.0049


--------------------------------------------------------------------------------------------------------------------------
### Let's try to solve the problem by two different methods:
1. `AeroBuildUp` is mostly built on [DATCOM Digital](https://www.pdas.com/datcom.html)
2. `AVL`

Then we will compare the results

In [50]:
opti2 = asb.Opti()
all_op_point_abup = asb.OperatingPoint(   # This is a vague operating point that doesn't specify any alpha or velocity, ...
                                          # ... They will be determined later when optimizing the solution
    atmosphere=atm,
    velocity=opti2.variable(
        init_guess=14,
        lower_bound=4, 
        upper_bound=50,
    ),
    alpha=opti2.variable(
        init_guess=0,
        lower_bound=-5,
        upper_bound=10,
    )
)
abup_results = asb.AeroBuildup(airplane=trainer, op_point=all_op_point_abup).run()
abup_L = abup_results["L"]   # lift force [N] computed via AeroBuildUp
abup_D = abup_results["D"]   # drag force [N] computed via AeroBuildUp
abup_Cm = abup_results["Cm"] # Moment Coefficient computed via AeroBuildUp
opti2.minimize((abup_Cm - 0)**2 + (abup_L - W)**2)
sol2 = opti2.solve()                    # solve the optimization problem and assign it to `sol` variable
abup_cruise_results = asb.AeroBuildup(airplane=trainer, op_point=sol2.value(all_op_point_abup)).run()
abup_cruise_aoa = sol2.value(all_op_point_abup).alpha
abup_cruise_v = sol2.value(all_op_point_abup).velocity
abup_cruise_cl = abup_cruise_results['CL'][0]
abup_cruise_cd = abup_cruise_results['CD'][0]
print(abup_cruise_results['Cm'])

This is Ipopt version 3.14.11, running with linear solver MUMPS 5.4.1.

Number of nonzeros in equality constraint Jacobian...:        0
Number of nonzeros in inequality constraint Jacobian.:        4
Number of nonzeros in Lagrangian Hessian.............:        3

Total number of variables............................:        2
                     variables with only lower bounds:        0
                variables with lower and upper bounds:        0
                     variables with only upper bounds:        0
Total number of equality constraints.................:        0
Total number of inequality constraints...............:        4
        inequality constraints with only lower bounds:        2
   inequality constraints with lower and upper bounds:        0
        inequality constraints with only upper bounds:        2

iter    objective    inf_pr   inf_du lg(mu)  ||d||  lg(rg) alpha_du alpha_pr  ls
   0  3.1580512e+01 0.00e+00 3.33e+01   0.0 0.00e+00    -  0.00e+00 0.00e+00 

In [52]:
# AeroBuildUp without fuselage
trainer_without_fuselage = asb.Airplane(
    name = 'trainer',
    xyz_ref=[0.073,0,-0.05],
    s_ref=wing.area(),
    b_ref=wing.span(),
    wings = [
        wing, # main wing
        htail.translate([612.34/1000,0,-0.025]), # Horizontal Tail (translated with L=Tail arm)
        vtail.translate([612.34/1000,0,-0.025])  # Vertical Tail (translated with L=Tail arm)
    ],
)
opti22 = asb.Opti()
all_op_point_abup2 = asb.OperatingPoint(   # This is a vague operating point that doesn't specify any alpha or velocity, ...
                                          # ... They will be determined later when optimizing the solution
    atmosphere=atm,
    velocity=opti22.variable(
        init_guess=14,
        lower_bound=13, 
        upper_bound=50,
    ),
    alpha=opti22.variable(
        init_guess=0,
        lower_bound=-1,
        upper_bound=10,
    )
)
abup_results2 = asb.AeroBuildup(airplane=trainer_without_fuselage, op_point=all_op_point_abup2).run()
abup_L2 = abup_results2["L"]   # lift force [N] computed via AeroBuildUp
abup_D2 = abup_results2["D"]   # drag force [N] computed via AeroBuildUp
abup_Cm2 = abup_results2["Cm"] # Moment Coefficient computed via AeroBuildUp
opti22.minimize((abup_Cm2 - 0)**2 + (abup_L2 - W)**2)    # Moment = 0
sol22 = opti22.solve()                    # solve the optimization problem and assign it to `sol` variable
abup_cruise_results2 = asb.AeroBuildup(airplane=trainer_without_fuselage, op_point=sol22.value(all_op_point_abup2)).run()
abup_cruise_aoa2 = sol22.value(all_op_point_abup2).alpha
abup_cruise_v2 = sol22.value(all_op_point_abup2).velocity
abup_cruise_cl2 = abup_cruise_results2['CL'][0]
abup_cruise_cd2 = abup_cruise_results['CD'][0]
print("------------------------- cruise conditions from AeroBuildUp: Fuselage | Without Fuselage -------------------------")
print(f"Angle of attack: {abup_cruise_aoa:.4f} | {abup_cruise_aoa2:.4f} degree ")
print(f"Velocity: {abup_cruise_v:.4f} | {abup_cruise_v2:.4f} m/s")
print(f"CL: {abup_cruise_cl:.4f} | {abup_cruise_cl2:.4f}")
print(f"CD: {abup_cruise_cd:.4f} | {abup_cruise_cd2:.4f}")

This is Ipopt version 3.14.11, running with linear solver MUMPS 5.4.1.

Number of nonzeros in equality constraint Jacobian...:        0
Number of nonzeros in inequality constraint Jacobian.:        4
Number of nonzeros in Lagrangian Hessian.............:        3

Total number of variables............................:        2
                     variables with only lower bounds:        0
                variables with lower and upper bounds:        0
                     variables with only upper bounds:        0
Total number of equality constraints.................:        0
Total number of inequality constraints...............:        4
        inequality constraints with only lower bounds:        2
   inequality constraints with lower and upper bounds:        0
        inequality constraints with only upper bounds:        2

iter    objective    inf_pr   inf_du lg(mu)  ||d||  lg(rg) alpha_du alpha_pr  ls
   0  3.1841099e+01 0.00e+00 3.33e+01   0.0 0.00e+00    -  0.00e+00 0.00e+00 

> NOTE the big difference in the predicted CD by the AeroBuildUp method and the VLM method. Let's move on and see what does AVL has to offer us then we'll go through each result interpretation

### Running Lifting Line Thoery (Nonlinear and Quasi-linear)

In [53]:
opti4 = asb.Opti()
all_op_point_llt = asb.OperatingPoint(   # This is a vague operating point that doesn't specify any alpha or velocity, ...
                                          # ... They will be determined later when optimizing the solution
    atmosphere=atm,
    velocity=opti4.variable(
        init_guess=14,
        lower_bound=13, 
        upper_bound=50,
    ),
    alpha=opti4.variable(
        init_guess=0,
        lower_bound=-1,
        upper_bound=10,
    )
)
llt_results = asb.LiftingLine(airplane=trainer, op_point=all_op_point_llt,spanwise_resolution=15).run()
llt_L = llt_results["L"]   # lift force [N] computed via AeroBuildUp
llt_D = llt_results["D"]   # drag force [N] computed via AeroBuildUp
llt_Cm = llt_results["m_b"] # Moment Coefficient computed via AeroBuildUp
opti4.subject_to(llt_L == W)           # Lift = Weight Constraint
opti4.subject_to(llt_Cm <= 1e-18)      # Moment = 0
sol4 = opti4.solve()                    # solve the optimization problem and assign it to `sol` variable
llt_cruise_results = asb.LiftingLine(airplane=trainer, op_point=sol4.value(all_op_point_llt),spanwise_resolution=15).run()
llt_cruise_aoa4 = sol4.value(all_op_point_llt).alpha
llt_cruise_v4 = sol4.value(all_op_point_llt).velocity
llt_cruise_cl4 = llt_cruise_results['CL']
llt_cruise_cd4 = llt_cruise_results['CD']

This is Ipopt version 3.14.11, running with linear solver MUMPS 5.4.1.

Number of nonzeros in equality constraint Jacobian...:        2
Number of nonzeros in inequality constraint Jacobian.:        6
Number of nonzeros in Lagrangian Hessian.............:        3

Total number of variables............................:        2
                     variables with only lower bounds:        0
                variables with lower and upper bounds:        0
                     variables with only upper bounds:        0
Total number of equality constraints.................:        1
Total number of inequality constraints...............:        5
        inequality constraints with only lower bounds:        2
   inequality constraints with lower and upper bounds:        0
        inequality constraints with only upper bounds:        3

iter    objective    inf_pr   inf_du lg(mu)  ||d||  lg(rg) alpha_du alpha_pr  ls
   0  0.0000000e+00 5.03e-01 1.77e-01   0.0 0.00e+00    -  0.00e+00 0.00e+00 

In [ ]:
# Nonlinear LLT
optii44 = asb.Opti()
all_op_point_llt2 = asb.OperatingPoint(   # This is a vague operating point that doesn't specify any alpha or velocity, ...
                                          # ... They will be determined later when optimizing the solution
    atmosphere=atm,
    velocity=optii44.variable(
        init_guess=14,
        lower_bound=13, 
        upper_bound=50,
    ),
    alpha=optii44.variable(
        init_guess=0,
        lower_bound=-1,
        upper_bound=10,
    )
)
llt_results2 = asb.NonlinearLiftingLine(airplane=trainer, op_point=all_op_point_llt2,opti=optii44,spanwise_resolution=15).run(solve=False)
llt_L2 = llt_results2["L"]   # lift force [N] computed via AeroBuildUp
llt_D2 = llt_results2["D"]   # drag force [N] computed via AeroBuildUp
llt_Cm2 = llt_results2["m_b"] # Moment Coefficient computed via AeroBuildUp
optii44.subject_to(llt_L2 == W)           # Lift = Weight Constraint
optii44.subject_to(llt_Cm2 <= 1e-18)      # Moment = 0
sol44 = optii44.solve()                    # solve the optimization problem and assign it to `sol` variable
llt_cruise_results44 = asb.NonlinearLiftingLine(airplane=trainer, op_point=sol44.value(all_op_point_llt2),spanwise_resolution=15).run()
llt_cruise_aoa44 = sol44.value(all_op_point_llt2).alpha
llt_cruise_v44 = sol44.value(all_op_point_llt2).velocity
llt_cruise_cl44 = llt_cruise_results44['CL']
llt_cruise_cd44 = llt_cruise_results44['CD']


print("------------------------- cruise conditions from Lifting Line Theory: Linear | Nonlinear -------------------------")
print(f"Angle of attack: {llt_cruise_aoa4:.4f} | {llt_cruise_aoa44:.4f} degree ")
print(f"Velocity: {llt_cruise_v4:.4f} | {llt_cruise_v44:.4f} m/s")
print(f"CL: {llt_cruise_cl4:.4f} | {llt_cruise_cl44:.4f}")
print(f"CD: {llt_cruise_cd4:.4f} | {llt_cruise_cd44:.4f}")

This is Ipopt version 3.14.11, running with linear solver MUMPS 5.4.1.

Number of nonzeros in equality constraint Jacobian...:       77
Number of nonzeros in inequality constraint Jacobian.:       81
Number of nonzeros in Lagrangian Hessian.............:     3003

Total number of variables............................:       77
                     variables with only lower bounds:        0
                variables with lower and upper bounds:        0
                     variables with only upper bounds:        0
Total number of equality constraints.................:        1
Total number of inequality constraints...............:        5
        inequality constraints with only lower bounds:        2
   inequality constraints with lower and upper bounds:        0
        inequality constraints with only upper bounds:        3



### Running AVL Analysis
You need to have AVL downloaded and added to the system PATH, if not specify the executable location when defining the AVL analysis (commented down below)

`working_directory=$PATH/TO/AVL$`

In [5]:
from tqdm import tqdm

velocity = np.linspace(10, 25, 70)
alpha = np.linspace(-5, 10, 70)

n_vel, n_alpha = len(velocity), len(alpha)

avl_L = np.empty((n_vel, n_alpha))
avl_cl = np.empty((n_vel, n_alpha))
avl_cd = np.empty((n_vel, n_alpha))
avl_D = np.empty((n_vel, n_alpha))
avl_cm = np.empty((n_vel, n_alpha))

for i, v in enumerate(tqdm(velocity, desc="Velocity sweep")):
    for j, aoa in enumerate(alpha):
        op_point = asb.OperatingPoint(
            atmosphere=atm,
            velocity=v,
            alpha=aoa,
        )
        results = asb.AVL(
            airplane=trainer_without_fuselage,
            op_point=op_point,
            avl_command='avl',
            timeout = 20,
        ).run()

        avl_L[i, j] = results['L']
        avl_D[i, j] = results['D']
        avl_cl[i, j] = results['CL']
        avl_cd[i, j] = results['CD']
        avl_cm[i, j] = results['Cm']


Velocity sweep: 100%|██████████████████████████████████████████████████████████████████| 70/70 [27:27<00:00, 23.54s/it]


In [ ]:
!{sys.executable} -m pip install scipy

In [7]:
from scipy.interpolate import RegularGridInterpolator
import numpy as np
from scipy.optimize import minimize

# Interpolators for Lift and Moment
interp_L = RegularGridInterpolator((velocity, alpha), avl_L.T)
interp_Cm = RegularGridInterpolator((velocity, alpha), avl_cm.T)

def trim_cost(x, weight):
    V, aoa = x  # x = [velocity, aoa]
    if not (velocity[0] <= V <= velocity[-1] and alpha[0] <= aoa <= alpha[-1]):
        return 1e9  # penalize if outside interpolation bounds

    L = interp_L([V, aoa])
    Cm = interp_Cm([V, aoa])
    return abs(Cm)

def trim_cost2(x, weight):
    V, aoa = x  # x = [velocity, aoa]
    if not (velocity[0] <= V <= velocity[-1] and alpha[0] <= aoa <= alpha[-1]):
        return 1e9  # penalize if outside interpolation bounds

    L = interp_L([V, aoa])
    Cm = interp_Cm([V, aoa])
    return abs(L-weight)


x0 = [19, 5]

result = minimize(trim_cost, x0, args=(W,), bounds=[(velocity[0], velocity[-1]), (alpha[0], alpha[-1])])
result2 = minimize(trim_cost2, x0, args=(W,), bounds=[(velocity[0], velocity[-1]), (alpha[0], alpha[-1])])

trim_velocity, trim_aoa = result.x
L_at_trim = interp_L(result.x) / 9.81
Cm_at_trim = interp_Cm(result.x)

trim_velocity2, trim_aoa2 = result2.x
L_at_trim2 = interp_L(result2.x) / 9.81
Cm_at_trim2 = interp_Cm(result2.x)
print(L_at_trim)
print(Cm_at_trim)
print(L_at_trim2)
print(Cm_at_trim2)
"""
print(f"Trim point found:")
print(f"→ Velocity: {trim_velocity:.2f} m/s")
print(f"→ AoA: {trim_aoa:.2f} degrees")
print(f"→ Lift: {L_at_trim:.2f} kg")
print(f"→ Cm: {Cm_at_trim:.4f}")"""


[7.65234392]
[1.44576985e-11]
[1.3]
[0.04800823]


'\nprint(f"Trim point found:")\nprint(f"→ Velocity: {trim_velocity:.2f} m/s")\nprint(f"→ AoA: {trim_aoa:.2f} degrees")\nprint(f"→ Lift: {L_at_trim:.2f} kg")\nprint(f"→ Cm: {Cm_at_trim:.4f}")'

In [ ]:
x = np.where((avl_L - W < 1e-6))[0]
y = np.where((avl_L - W < 1e-6))[1]
cms = []
for i in x:
    for j in y:
        if abs(avl_cm[i,j]) < 1e-1:
            print(avl_cm[i,j])
            print(i,j)
        else: cms.append(abs(avl_cm[i,j]))

print(min(cms))

0.067
0 0
0.06641
0 1
0.06578
0 2
0.06514
0 3
0.06447
0 4
0.06377
0 5
0.06305
0 6
0.06231
0 7
0.06155
0 8
0.06076
0 9
0.05994
0 10
0.0591
0 11
0.05824
0 12
0.05736
0 13
0.05645
0 14
0.05552
0 15
0.05456
0 16
0.05358
0 17
0.05258
0 18
0.05156
0 19
0.05051
0 20
0.04944
0 21
0.04834
0 22
0.04722
0 23
0.04608
0 24
0.04492
0 25
0.04373
0 26
0.04252
0 27
0.04129
0 28
0.04003
0 29
0.03875
0 30
0.03745
0 31
0.03613
0 32
0.03478
0 33
0.03342
0 34
0.03203
0 35
0.03061
0 36
0.02918
0 37
0.02772
0 38
0.02625
0 39
0.067
0 0
0.06641
0 1
0.06578
0 2
0.06514
0 3
0.06447
0 4
0.06377
0 5
0.06305
0 6
0.06231
0 7
0.06155
0 8
0.06076
0 9
0.05994
0 10
0.0591
0 11
0.05824
0 12
0.05736
0 13
0.05645
0 14
0.05552
0 15
0.05456
0 16
0.05358
0 17
0.05258
0 18
0.05156
0 19
0.05051
0 20
0.04944
0 21
0.04834
0 22
0.04722
0 23
0.04608
0 24
0.04492
0 25
0.04373
0 26
0.04252
0 27
0.04129
0 28
0.04003
0 29
0.03875
0 30
0.03745
0 31
0.03613
0 32
0.03478
0 33
0.03342
0 34
0.03203
0 35
0.03061
0 36
0.02918
0 37
0.02772
0 38

In [94]:
x = np.where((avl_cm < 1e-2))[0]
y = np.where((avl_cm < 1e-2))[1]
L = []
for i in x:
    for j in y:
        if abs(avl_L[i,j] - W)/9.81 < 0.1:
            print(avl_L[i,j]/9.81)
            print(i,j)
        else: L.append(abs(avl_L[i,j] - W))

print(min(L)/9.81)

0.5765173739918832
